In [2]:
!pip install pyLDAvis

You should consider upgrading via the 'c:\users\jonat\anaconda3\python.exe -m pip install --upgrade pip' command.


In [3]:
import pandas as pd
import re
import os
from pprint import pprint

# Gensim for topic modeling
import gensim
from gensim.utils import simple_preprocess
from gensim import matutils, models
import gensim.corpora as corpora
from gensim.models import CoherenceModel

# Plotting tools
import pyLDAvis
import pyLDAvis.gensim_models # don't skip this
import matplotlib.pyplot as plt
%matplotlib inline

import warnings
warnings.filterwarnings('ignore')

In [80]:
base_directory = "C:/Users/jonat/Documents/github/job-posting-analysis"


directory = os.chdir(f"{base_directory}/data/cleaned/")
files = os.listdir(".")
files


monster_df = pd.read_csv('All_MonsterSg.csv') 
monster_df.head(3)

job_title               company  \
0                         Senior Python Developer                  Citi   
1  Senior Partner Solutions Architect (Microsoft)                Amazon   
2                                   IT Technician  Ascend Com Pte. Ltd.   

               salary   job_type years_experience  \
0                 NaN  permanent              NaN   
1                 NaN  permanent              NaN   
2  ['24000', '36000']  permanent       ['2', '5']   

                                          tech_stack  \
0                                                NaN   
1                                                NaN   
2  ['Switches', 'Mac', 'Windows 10', 'Cloud Compu...   

                                     job_description  \
0  Job Description :\r\n\r\nJob Purpose:\r\nWe ar...   
1  Job Description :\r\nJob summary\r\nDESCRIPTIO...   
2  Responsibilities:\r\nProvide helpdesk support ...   

                                    industry function  \
0  ['Banking/Accounting/Financial Services']   ['IT']   
1                    ['Internet/E-commerce']   ['IT']   
2                                  ['Other']   ['IT']   

                              roles date_posted  \
0  ['Software Engineer/Programmer']  2022-02-18   
1  ['Software Engineer/Programmer']  2022-02-18   
2   ['Other Software/Hardware/EDP']  2022-02-19   

                                                 url  
0  https://www.monster.com.sg/seeker/job-details?...  
1  https://www.monster.com.sg/seeker/job-details?...  
2  https://www.monster.com.sg/seeker/job-details?...

In [6]:
monster_df.job_description[0]

"Job Description :\r\n\r\nJob Purpose:\r\nWe are looking for a Skilled Python Developer who can design and build best-in-class data driven applications for front office teams across the global markets business. You will work closely with product owners, project managers, developers, data scientists and other team members to deliver solutions through new and existing channels. You will need to be confident to work with senior business stakeholders to understand their requirements and to ideate and drive the development of innovative technology solutions in a timely manner.\r\n\r\nJob Background/context:\r\nWe believe the future is here with us! Home to where we define, ideate, develop and distribute production-ready financial solutions of far-reaching impact. And right now, the door is open to help develop the future of our technology for a truly global client base. This means collaborating with the keenest minds in data science, big data, software engineering, web development, UX desig

In [11]:
re.sub('\n', "", '\r\n\r\nJob Purpose:\r\nWe are looking f')

'\r\nJob Purpose:\r\nWe are looking f'

In [12]:
re.sub('\r','','\r\nJob Purpose:\r\nWe are looking f')

'\nJob Purpose:\nWe are looking f'

In [23]:
import re
x = '\r\n\r\nJob Purpose:\r\nWe are -------------------!!@#!!--------------looking f??'
x= x.replace("\r", "")
x = x.replace ("\n", "")
x = x.replace("-", "")

x =re.sub(r'[^\w\s]', '', x)

x

'Job PurposeWe are looking f'

In [72]:
import nltk
nltk.download('wordnet')
nltk.download('omw-1.4')
from nltk.stem import WordNetLemmatizer
lemmatizer = WordNetLemmatizer()

[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\jonat\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\jonat\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping corpora\omw-1.4.zip.


In [120]:
from nltk.corpus import stopwords
stop_words = stopwords.words('english')
stop_words.extend(['from', 'subject', 're', 'edu', 'use', 'not', 'would', 'say', 'could', '_', 'be', 'know', 'good', 'go', 'get', 'do', 'done', 'try', 'many', 'some', 'nice', 'thank', 'think', 'see', 'rather', 'easy', 'easily', 'lot', 'lack', 'make', 'want', 'seem', 'run', 'need', 'even', 'right', 'line', 'even', 'also', 'may', 'take', 'come'])

def clean_job_description(x):

    x = re.sub(r'\w*\d\w*','', str(x))
    x = x.replace("\r", " ")
    x = x.replace ("\n", " ")
    x = re.sub(r'[^\w\s]', '', x)
    x = x.lower()
    x = x.split(' ')
    return x

def remove_stop_words(x,stop_words):
    cleaned_list = []
    for i in x: 
        if i != "" and i not in stop_words:
            cleaned_list.append(lemmatizer.lemmatize(i))
    
    return cleaned_list

In [122]:
monster_job_description = monster_df['job_description']
monster_job_description = monster_job_description.apply(lambda x: clean_job_description(x))
monster_job_description = monster_job_description.apply(lambda x: remove_stop_words(x,stop_words))
monster_job_description.tail(10)
# monster_job_description = monster_job_description.to_frame(name='job_description')
# monster_job_description

8405    [job, description, support, marketing, manager...
8406    [job, responsibility, demonstrate, knowledge, ...
8407    [android, java, kotlin, spring, boot, mysql, d...
8408    [business, used, rely, technology, business, t...
8409    [toff, technology, toff, provide, solution, de...
8410    [job, description, responsible, overall, platf...
8411    [job, description, senior, developer, primary,...
8412    [location, paya, lebar, working, hour, shift, ...
8413    [director, responsible, managing, large, compl...
8414    [company, client, market, leader, within, indu...
Name: job_description, dtype: object

In [123]:
monster_job_description.tolist()

[['job',
  'description',
  'job',
  'purpose',
  'looking',
  'skilled',
  'python',
  'developer',
  'design',
  'build',
  'bestinclass',
  'data',
  'driven',
  'application',
  'front',
  'office',
  'team',
  'across',
  'global',
  'market',
  'business',
  'work',
  'closely',
  'product',
  'owner',
  'project',
  'manager',
  'developer',
  'data',
  'scientist',
  'team',
  'member',
  'deliver',
  'solution',
  'new',
  'existing',
  'channel',
  'confident',
  'work',
  'senior',
  'business',
  'stakeholder',
  'understand',
  'requirement',
  'ideate',
  'drive',
  'development',
  'innovative',
  'technology',
  'solution',
  'timely',
  'manner',
  'job',
  'backgroundcontext',
  'believe',
  'future',
  'u',
  'home',
  'define',
  'ideate',
  'develop',
  'distribute',
  'productionready',
  'financial',
  'solution',
  'farreaching',
  'impact',
  'door',
  'open',
  'help',
  'develop',
  'future',
  'technology',
  'truly',
  'global',
  'client',
  'base',
  'mea

## Create Corpus

In [124]:
def str_to_list(text):
    text = text[1:len(text)-1]
    #text_list = text.split(',')
    text_list = [text.strip()[1:-1] for text in text]
    return text_list

In [125]:
data_lemmatized = monster_job_description.tolist()
#data_lemmatized = [str_to_list(text) for text in data_lemmatized]
print(data_lemmatized[:10])

[['job', 'description', 'job', 'purpose', 'looking', 'skilled', 'python', 'developer', 'design', 'build', 'bestinclass', 'data', 'driven', 'application', 'front', 'office', 'team', 'across', 'global', 'market', 'business', 'work', 'closely', 'product', 'owner', 'project', 'manager', 'developer', 'data', 'scientist', 'team', 'member', 'deliver', 'solution', 'new', 'existing', 'channel', 'confident', 'work', 'senior', 'business', 'stakeholder', 'understand', 'requirement', 'ideate', 'drive', 'development', 'innovative', 'technology', 'solution', 'timely', 'manner', 'job', 'backgroundcontext', 'believe', 'future', 'u', 'home', 'define', 'ideate', 'develop', 'distribute', 'productionready', 'financial', 'solution', 'farreaching', 'impact', 'door', 'open', 'help', 'develop', 'future', 'technology', 'truly', 'global', 'client', 'base', 'mean', 'collaborating', 'keenest', 'mind', 'data', 'science', 'big', 'data', 'software', 'engineering', 'web', 'development', 'ux', 'design', 'doer', 'lookin

In [127]:
# Create Dictionary
id2word = corpora.Dictionary(data_lemmatized)
# Filter out tokens that appear in only 1 documents and appear in more than 90% of the documents
id2word.filter_extremes(no_below=2, no_above=0.9)
# Create Corpus
texts = data_lemmatized
# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]

In [128]:
# Create a dictionary representation of the documents. Each word gets an id
print('Sample word to id mappings:\n', list(id2word.items())[:50])
print()
print('Total Vocabulary Size:', len(id2word))

Sample word to id mappings:
 [(0, 'able'), (1, 'accommodation'), (2, 'achieve'), (3, 'across'), (4, 'action'), (5, 'affirmative'), (6, 'agile'), (7, 'ahead'), (8, 'alone'), (9, 'analytics'), (10, 'andor'), (11, 'angular'), (12, 'ant'), (13, 'anywhere'), (14, 'apac'), (15, 'applicant'), (16, 'application'), (17, 'apply'), (18, 'architecture'), (19, 'array'), (20, 'associated'), (21, 'aws'), (22, 'backgroundcontext'), (23, 'base'), (24, 'based'), (25, 'believe'), (26, 'best'), (27, 'bestinclass'), (28, 'bi'), (29, 'big'), (30, 'bold'), (31, 'boot'), (32, 'bring'), (33, 'broad'), (34, 'broader'), (35, 'build'), (36, 'business'), (37, 'caching'), (38, 'capability'), (39, 'capable'), (40, 'career'), (41, 'cd'), (42, 'centric'), (43, 'change'), (44, 'channel'), (45, 'ci'), (46, 'citi'), (47, 'citigroup'), (48, 'clear'), (49, 'client')]

Total Vocabulary Size: 20859


## Building LDA Model

### Hypertuning Model Parameters

In [115]:
# supporting function
def compute_evaluation_values(corpus, dictionary, k):
    
    lda_model = gensim.models.LdaMulticore(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=k, 
                                           random_state=100,
                                           chunksize=100,
                                           passes=20,
                                           per_word_topics=True)
    
    coherence_model_lda = CoherenceModel(model=lda_model, texts=data_lemmatized, dictionary=id2word, coherence='c_v')
    perplexity = lda_model.log_perplexity(corpus)
    
    return [coherence_model_lda.get_coherence(), perplexity]

In [116]:
# Iterate over possible number of topics.
topic_param = []
coherence_score = []
perplexity_score = []

for k in range(2, 20):
    print('topic number: ', k)
    ev = compute_evaluation_values(corpus=corpus, dictionary=id2word, k=k)
    coherence_score.append(ev[0])
    perplexity_score.append(ev[1])
    print('Coherence Score: ', ev[0])
    print('Perplexity Score: ', ev[1])
    print()
    
    topic_param.append(k)

topic number:  2
Coherence Score:  0.3093766410927574
Perplexity Score:  -7.400126654740014

topic number:  3
Coherence Score:  0.341059528747283
Perplexity Score:  -7.365839701947773

topic number:  4
Coherence Score:  0.34287242105713067
Perplexity Score:  -7.337724857097807

topic number:  5
Coherence Score:  0.3609144719344628
Perplexity Score:  -7.317815284970022

topic number:  6
Coherence Score:  0.3839671078196105
Perplexity Score:  -7.298109180056135

topic number:  7
Coherence Score:  0.3595306302033672
Perplexity Score:  -7.303502334172618

topic number:  8
Coherence Score:  0.36624905748309233
Perplexity Score:  -7.308128055829262

topic number:  9
Coherence Score:  0.37569332098264174
Perplexity Score:  -7.338709622056607

topic number:  10
Coherence Score:  0.35837355940832905
Perplexity Score:  -7.370840543001459

topic number:  11
Coherence Score:  0.3624673563890152
Perplexity Score:  -7.413912840267222

topic number:  12
Coherence Score:  0.3636151981565799
Perplexity

KeyboardInterrupt: 

In [ ]:
# Show graph
plt.figure(figsize=(16, 8))
plt.plot(topic_param, coherence_score)

plt.title("Choosing Optimal LDA Model")
plt.xlabel("Num Topics")
plt.ylabel("Coherence Scores")
plt.show()

### Final LDA Model

In [ ]:
ntopics = 5

lda_model = gensim.models.LdaMulticore(corpus=corpus,
                                       id2word=id2word,
                                       num_topics=ntopics_des_name, 
                                       random_state=100,
                                       chunksize=100,
                                       passes=20,
                                       per_word_topics=True)

In [ ]:
# Print the Keyword in the topics
pprint(lda_model.print_topics())
doc_lda = lda_model[corpus]

In [ ]:
def Sort_Tuple(tup):  
    return(sorted(tup, key = lambda x: x[1], reverse = True))

In [ ]:
topic_num = []
print(lda_model.get_document_topics(corpus))
for n in range(len(df_final)):
    get_document_topics = lda_model.get_document_topics(corpus[n])
    sorted_doc_topics = Sort_Tuple(get_document_topics)
    all_topic = []
    for i in sorted_doc_topics:
        all_topic.append(i[0])
    topic_num.append(all_topic)

In [ ]:
monster_df['Topic'] = topic_num

In [ ]:
monster_df

## Visualisation

In [ ]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model_des_name, corpus, id2word)
vis

In [ ]:
from collections import Counter

topics = lda_model_des_name.show_topics(num_topics=ntopics_des_name, formatted=False)
data_flat = [w for w_list in data_lemmatized for w in w_list]
counter = Counter(data_flat)

out = []
for i, topic in topics:
    for word, weight in topic:
        out.append([word, i , weight, counter[word]])

df = pd.DataFrame(out, columns=['word', 'topic_id', 'importance', 'word_count'])        

# Plot Word Count and Weights of Topic Keywords
fig, axes = plt.subplots(10, 2, figsize=(10,20), dpi=160)
cols = ['#008080', '#A52A2A', '#DC143C', '#800000', '#006400', '#556b2f', '#002366', '#ff8c00', '#FF1493', '#9400D3',
        '#ba55d3', '#b8860b', '#C71585', '#00ff7f', '#00004C', '#00008B', '#B8860B', '#DEB887', '#8A2BE2', '#1b364a']

for i, ax in enumerate(axes.flatten()):
    if i > ntopics_des_name - 1: # break when all topics are shown
        break
    ax.bar(x='word', height="word_count", data=df.loc[df.topic_id==i, :], color=cols[i], width=0.5, alpha=0.3, label='Word Count')
    ax_twin = ax.twinx()
    ax_twin.bar(x='word', height="importance", data=df.loc[df.topic_id==i, :], color=cols[i], width=0.2, label='Weights')
    ax.set_ylabel('Word Count', color=cols[i])
    ax.set_title('Topic: ' + str(i), color=cols[i], fontsize=16)
    ax.tick_params(axis='y', left=False)
    ax.set_xticklabels(df.loc[df.topic_id==i, 'word'], rotation=30, horizontalalignment= 'right')
    ax.legend(loc='upper left'); ax_twin.legend(loc='upper right')


fig.tight_layout(w_pad=2)    
fig.suptitle('Word Count and Importance of Topic Keywords', fontsize=22, y=1.05)    
plt.show()